In [2]:
# relacionar dado espacial de NDVI com a produtividade
import matplotlib.pyplot as plt
import rasterio
import rasterio.mask
import numpy as np
import pandas as pd
from rasterio.plot import show as show_raster # To avoid conflict with plt.show()
import geopandas as gpd
import sklearn
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import train_test_split # Standard split, but we'll do chronological
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error

# funcoes
def calculate_spatial_stats(raster_filepath, stats):
    """
    Calculates the spatial average of pixel values in the first band of a raster.

    Args:
        raster_filepath (str): The path to the raster file.

    Returns:
        float: The spatial average, or None if an error occurs.
    """
        
    try:
        with rasterio.open(raster_filepath) as src:
            data_array = src.read(1)
            nodata_value = src.nodata

            if nodata_value is not None:
                masked_data = np.ma.masked_equal(data_array, nodata_value, copy=False)
                
                # Calculate the mean of the unmasked (valid) pixel values
                if(stats == 'mean'):
                    spatial_average = masked_data.mean()
                if(stats == 'max'):
                    spatial_average = masked_data.max()
                if(stats == 'min'):
                    spatial_average = masked_data.min()
                if(stats == 'var'):
                    spatial_average = masked_data.var()
            else:
                # If no NoData value is defined, assume all pixels are valid
                spatial_average = data_array.mean()
            
            return float(spatial_average) # Ensure return type is a standard float

    except rasterio.errors.RasterioIOError as e:
        print(f"Error opening or reading raster file: {e}")
        return None
    except Exception as e:
        print(f"An unexpected error occurred: {e}")
        return None

In [87]:
src_MT = rasterio.open('/home/jovyan/Desktop/enandes_v2/modelo_produtividade/dados_ndvi_pkl/ndvi_2021.tif')
primeira_banda = src_MT.read(1)
outra_banda = src_MT.read(22)

print(primeira_banda)
print(outra_banda)

# mean_ndvi = []
# years = 2021
# src_MT = rasterio.open('/home/jovyan/Desktop/enandes_v2/modelo_produtividade/dados_ndvi_pkl/ndvi_2021.tif')
# for bands in range(1,24):
#     src_MT = src_MT.read(bands)
#     mean_ndvi.append(calculate_spatial_stats(src_MT, 'mean'))

# print(mean_ndvi)

[[0.73692075 0.74595773 0.81703349 ... 0.81630677 0.7289525  0.72924539]
 [0.81812385 0.817886   0.82856882 ... 0.85035465 0.77461198 0.76161676]
 [0.8512406  0.87627632 0.83344066 ... 0.85950244 0.82085434 0.75672134]
 ...
 [0.8944     0.8974     0.8974     ... 0.50398359 0.49817421 0.51448337]
 [0.8897     0.8944     0.9011     ... 0.67992919 0.48526551 0.42837299]
 [0.9006     0.9008     0.9133     ... 0.83724936 0.74893148 0.7122    ]]
[[0.85041313 0.85053031 0.84991429 ... 0.61206442 0.6354718  0.69886496]
 [0.86474286 0.86662857 0.86303285 ... 0.68711439 0.63521608 0.6606329 ]
 [0.87057143 0.8686     0.8686     ... 0.80035624 0.66982372 0.75518612]
 ...
 [0.9058     0.9154     0.9182     ... 0.72215073 0.74463388 0.6904    ]
 [0.9048     0.88263115 0.9163     ... 0.676      0.7136     0.6991    ]
 [0.8973     0.9009     0.9176     ... 0.83332994 0.76130047 0.6745    ]]


In [75]:
# abrir dados
src = rasterio.open('/home/jovyan/Desktop/enandes_v2/modelo_produtividade/dados_ndvi_pkl/ndvi_2021_masked_AT_MT.tif')

print(f"Número de bandas: {src_MT.count}")
print(f"Altura: {src_MT.height} pixels")
print(f"Largura: {src_MT.width} pixels")
print(f"Sistema de Coordenadas (CRS): {src_MT.crs}")
print(f"Transformação (Affine): {src_MT.transform}")
print(f"Tipos de dados das bandas: {src_MT.dtypes}")

src = src_MT

Número de bandas: 23
Altura: 4800 pixels
Largura: 4800 pixels
Sistema de Coordenadas (CRS): EPSG:4326
Transformação (Affine): | 0.00, 0.00,-63.85|
| 0.00,-0.00,-10.00|
| 0.00, 0.00, 1.00|
Tipos de dados das bandas: ('float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64', 'float64')


In [76]:
# primeiro testar com a media
# abrir dados espaciais e calcular media
mean_ndvi = []
max_ndvi = []
min_ndvi = []
var_ndvi = []
for years in range(2001,2024):
    src = f'/home/jovyan/Desktop/enandes_v2/modelo_produtividade/dados_ndvi_pkl/ndvi_{years}_masked_AT_MT.tif' 
    mean_ndvi.append(calculate_spatial_stats(src, 'mean'))
    max_ndvi.append(calculate_spatial_stats(src, 'max'))
    min_ndvi.append(calculate_spatial_stats(src, 'min'))
    var_ndvi.append(calculate_spatial_stats(src, 'var'))

#print(mean_ndvi)

In [77]:
mean_ndvi = (np.array(pd.Series(mean_ndvi)))
print(mean_ndvi)

[0.77754802 0.81458389 0.79780186 0.79411401 0.80277716 0.77681128
 0.74423866 0.74001662 0.73513918 0.75624094 0.82749329 0.8010206
 0.83342082 0.83458789 0.80686004 0.78663406 0.84592384 0.83797839
 0.82193049 0.7087739  0.81993562 0.75722905 0.73669657]


In [60]:
produtividade = pd.read_csv('produtividade_area_AT_MT.txt', sep=',')
print(np.array(produtividade).reshape(-1))


[3.12 3.08 3.09 2.9  3.16 2.89 3.02 3.19 3.1  3.06 3.37 3.16 3.03 2.99
 3.06 2.98 3.38 3.45 3.34 3.65 3.3  3.3  3.71]


In [61]:
# testar modelo random forest

# --- 1. Data Loading and Preparation ---
np.random.seed(42) # for reproducibility
years = np.arange(2001, 2024) # 2001 to 2023
ndvi_values = np.array(pd.Series(mean_ndvi))
productivity_values = np.array(produtividade).reshape(-1)

df_ndvi = pd.DataFrame({'Year': years, 'NDVI': ndvi_values})
df_prod = pd.DataFrame({'Year': years, 'Productivity': productivity_values})

In [ ]:
# --- 2. Feature Engineering ---
# We want to predict Productivity(t) using NDVI(t) and lagged NDVI values.
# Let's create lagged features for NDVI.
# Number of lags to create
n_lags = 2 # e.g., NDVI(t-1), NDVI(t-2)

for i in range(1, n_lags + 1):
    df_merged[f'NDVI_L{i}'] = df_merged['NDVI'].shift(i)

# Optionally, you could also use lagged productivity as a feature:
# df_merged['Productivity_L1'] = df_merged['Productivity'].shift(1)

# Drop rows with NaN values resulting from creating lags
df_model_data = df_merged.dropna().reset_index(drop=True)

if df_model_data.empty:
    raise ValueError("Not enough data after creating lagged features and dropping NaNs. Consider fewer lags or more initial data.")

# Define features (X) and target (y)
# Features: Current NDVI and its lagged values
feature_columns = ['NDVI'] + [f'NDVI_L{i}' for i in range(1, n_lags + 1)]
# If using lagged productivity: feature_columns.append('Productivity_L1')

X = df_model_data[feature_columns]
y = df_model_data['Productivity']
years_for_model = df_model_data['Year'] # Keep track of years for plotting/analysis
